# Introduction

- Projet partiel présenté par: **François Pelletier**
- Matricule: **908144032**
- Dans le cadre du cours: **IFT-7025**


## Définitions

La **matrice de confusion** est un tableau où on décompte les valeurs réelle O et prédites S pour chaque observation du jeu de données dans un problème de classification. Par sa conception, on peut valider rapidement le nombre d'observations où la prédiction est égale à la valeur réelle sur la diagonale de la matrice. Par convention, on place les valeurs prédites à la verticale et les valeurs observées à l'horizontale. Lorsque le nombre de modalités de la variable prédite est de deux, on a un problème de classification binaire et on obtient alors le décompte des vrais positifs, faux positifs, faux négatifs et vrais négatifs.

La **précision** correspont à la proportion d'observations où la prédiction et la valeur réelle est dans une même classe par rapport au nombre d'observations où la prédiction est dans cette classe

$$ \text{Précision}_c =  \frac{\sum_{i=1}^N 1_{s_i=c}1_{o_i=c}}{\sum_{i=1}^N 1_{s_i=c}}$$

Le **rappel** correspond à la proportions d'observations où la prédiction est dans une classe par rapport au nombre d'observations où la valeur réelle est dans cette classe.

$$ \text{Rappel}_c =  \frac{\sum_{i=1}^N 1_{s_i=c}}{\sum_{i=1}^N 1_{o_i=c}}$$

## Librairies utilisées

Le project actuel est programmé dans le langage Python 3, et ce rapport est produit à l'aide de Jupyter Notebook. Seule les librairie standard `numpy` et `math` est utilisée, les autres ont été développées dans le cadre de ce projet.

In [46]:
# Librairies standard
import numpy as np
import math
# Librairies développées par l'étudiant
import load_datasets as ld
import metrics
import BayesNaif
import Knn

## Jeux de données

Ce projet utilise 3 jeux de données: [Iris](https://archive.ics.uci.edu/ml/datasets/Iris), [MONKS](https://archive.ics.uci.edu/ml/datasets/MONK's+Problems) et [Congressional Voting Records Dataset](https://archive.ics.uci.edu/ml/datasets/Congressional+Voting+Records). Pour les jeux qui ne sont pas déjà divisés en entrainement et test, on utilisera un ratio de 70% pour l'entrainement.

In [47]:
train1, train_labels1, test1, test_labels1 = ld.load_iris_dataset(train_ratio = 0.7)
train2, train_labels2, test2, test_labels2 = ld.load_monks_dataset(1)
train3, train_labels3, test3, test_labels3 = ld.load_monks_dataset(2)
train4, train_labels4, test4, test_labels4 = ld.load_monks_dataset(3)
train5, train_labels5, test5, test_labels5 = ld.load_congressional_dataset(train_ratio = 0.7)

# Algorithme des k plus proches voisins (kNN)

Dans cette section, on présente les résultats obtenus pour l'algorithme des k plus proches voisins. Ce n'est pas un algorithme d'apprentissage à proprement parler, car il n'y a aucun modèle d'entrainé. On prédit la classe d'un nouvel élément en recherchant les $k$ plus proches voisins selon une métrique choisie. Dans notre cas, nous utiliserons la distance de Minkowski, qui est une généralisation de la distance euclidienne et de la distance de Manhattan à l'aide d'un paramètre $p$. Pour nos besoins, on le fixe à $p=2$, soit la distance euclidienne.

$${\displaystyle D\left(X,Y\right)=\left(\sum _{i=1}^{N}|o_{i}-s_{i}|^{p}\right)^{1/p}}$$

On peut ainsi itérer sur différentes valeurs de ce paramètre pour trouver la mesure la plus adaptée au problème, tout en réutilisant la même fonction. Cette métrique s'utilise aurant pour des domaines de valeurs continus que discrets.

## Pseudocode

- Initialisation

```
k = 5
minkowski_p = 2
```

- Entrainement

```
Copier le jeu d'entrainement et les étiquettes d'entrainement dans la mémoire du modèle
```

- Prédiction
```
Pour une observation x_i:
    Entrainement <- Vrai si on fait le premier entrainement
    T = copie jeu d'entrainement
    L = copie des étiquettes d'entrainement
    K = tableau de paires (point, distance) de longueur k
    Si Entrainement:
        Enlever x de T et l'étiquette de x_i de L
    Pour chaque observation t_j, j=[1,k]) de T:
        d(x_i,t_i) = distance de Minkowski entre x_i et t_j
        K[j] <- (t_i,d(x_i,t_j)) 
    Pour chaque observation t_j, j=[k+1,N-1] de T:
        d(x,t_i) = distance de Minkowski entre x_i et t_j
        d_max <- distance maximum dans K
        pos_d_max <- position de d_max dans K
        Si d(x_i,t_j) < d_max
            Remplacer le point K[pos_d_max] par (t_j,d(x,t_j))
    s <- mode des valeurs des étiquettes des points dans K
    retourner s
```

- Test

```
Pour chaque observation x_i, i=1,N:
    S_i <- Prédiction(x_i)
M <- matrice de confusion avec les étiquettes d'entrainement et les étiquettes S
Calculer les métriques depuis M
```

- Validation croisée

```
K <- Valeurs à tester pour le nombre de voisins
Pour un jeu d'entrainement x
Permuter aléatoirement les nombre de 1 à N
Diviser la permutation en L groupes approximativement égaux
Pour l dans L:
    

Pour k dans K:
    Pour l dans L:
        Effectuer l'entrainement avec k voisins, x[sans l] comme jeu d'entrainement 
        Effectuer le test avec x[l] comme jeu de validation
        Calculer l'exactitude
    Prendre la moyenne des exactitudes
Prendre le k avec la meilleur exactitude moyenne
```

## Iris Dataset

On utilise 70% des données pour le jeu d'entrainement et 30% des données pour le jeu de test

On crée un premier modèle afin d'identifier la meilleure valeur de k

In [48]:
%%capture --no-display
findbest_Knn = Knn.Knn()
meilleur_k = findbest_Knn.set_best_k(train1, 
                                     train_labels1, 
                                     nb_split=5, 
                                     k_potentiel=range(2,12))

On crée maintenant un nouveau modèle où on initialise la valeur de K avec celle trouvée précédemment

In [49]:
myKnn = Knn.Knn(meilleur_k)

On effectue l'entrainement du modèle (la copie du jeu d'entrainement et des étiquettes en mémoire) et on obtient les mesures de validation pour ce jeu d'entraînement. Les valeurs des métriques de précision et de rappel sont calculées pour chacune des étiquettes.

In [50]:
training_iris_knn = myKnn.train(train1, train_labels1)

Matrice de confusion:
[[35.  0.  0.]
 [ 0. 32.  1.]
 [ 0.  4. 33.]]

Exactitude:
0.9523809523809523

Précision:
[1.0, 0.8888888888888888, 0.9705882352941176]

Rappel:
[1.0, 0.9696969696969697, 0.8918918918918919]

Calculé en:
0.10393261909484863s


On effectue maintenant le test avec l'échantillon de test

In [51]:
test_iris_knn = myKnn.test(test1, test_labels1)

Matrice de confusion:
[[15.  0.  0.]
 [ 0. 15.  2.]
 [ 0.  0. 13.]]

Exactitude:
0.9555555555555556

Précision:
[1.0, 1.0, 0.8666666666666667]

Rappel:
[1.0, 0.8823529411764706, 1.0]

Calculé en:
0.04592633247375488s


## Monks Dataset

### Premier sous-ensemble

- On identifie la meilleure valeur de k

In [52]:
findbest_Knn = Knn.Knn()
meilleur_k = findbest_Knn.set_best_k(train2, 
                                     train_labels2, 
                                     nb_split=5, 
                                     k_potentiel=range(2,12))

Le meilleur k est: 4
Calculé en 0.02272510528564453s


In [53]:
myKnn2 = Knn.Knn(meilleur_k)

- On effectue l'entrainement du modèle

In [54]:
training_monks1_knn = myKnn2.train(train2, train_labels2)

Matrice de confusion:
[[36. 26.]
 [19. 43.]]

Exactitude:
0.6370967741935484

Précision:
[0.6545454545454545, 0.6231884057971014]

Rappel:
[0.5806451612903226, 0.6935483870967742]

Calculé en:
0.12871980667114258s


- On effectue maintenant le test avec l'échantillon de test

In [55]:
test_monks1_knn = myKnn2.test(test2, test_labels2)

Matrice de confusion:
[[139.  77.]
 [ 49. 167.]]

Exactitude:
0.7083333333333334

Précision:
[0.7393617021276596, 0.6844262295081968]

Rappel:
[0.6435185185185185, 0.7731481481481481]

Calculé en:
0.4427499771118164s


### Second sous-ensemble

- On identifie la meilleure valeur de k

In [56]:
findbest_Knn = Knn.Knn()
meilleur_k = findbest_Knn.set_best_k(train3, 
                                     train_labels3, 
                                     nb_split=5, 
                                     k_potentiel=range(2,12))

Le meilleur k est: 3
Calculé en 0.04257488250732422s


In [57]:
myKnn3 = Knn.Knn(meilleur_k)

- On effectue l'entrainement du modèle

In [58]:
training_monks2_knn = myKnn3.train(train3, train_labels3)

Matrice de confusion:
[[105.   0.]
 [ 63.   1.]]

Exactitude:
0.6272189349112426

Précision:
[0.625, 1.0]

Rappel:
[1.0, 0.015625]

Calculé en:
0.2338266372680664s


- On effectue maintenant le test avec l'échantillon de test

In [59]:
test_monks2_knn = myKnn3.test(test3, test_labels3)

Matrice de confusion:
[[286.   4.]
 [129.  13.]]

Exactitude:
0.6921296296296297

Précision:
[0.689156626506024, 0.7647058823529411]

Rappel:
[0.9862068965517241, 0.09154929577464789]

Calculé en:
0.5991506576538086s


### Troisième sous-ensemble

- On identifie la meilleure valeur de k

In [60]:
findbest_Knn = Knn.Knn()
meilleur_k = findbest_Knn.set_best_k(train4, 
                                     train_labels4, 
                                     nb_split=5, 
                                     k_potentiel=range(2,12))

Le meilleur k est: 3
Calculé en 0.02377629280090332s


In [61]:
myKnn4 = Knn.Knn(meilleur_k)

- On effectue l'entrainement du modèle

In [62]:
training_monks3_knn = myKnn4.train(train4, train_labels4)

Matrice de confusion:
[[40. 22.]
 [16. 44.]]

Exactitude:
0.6885245901639344

Précision:
[0.7142857142857143, 0.6666666666666666]

Rappel:
[0.6451612903225806, 0.7333333333333333]

Calculé en:
0.1286787986755371s


- On effectue maintenant le test avec l'échantillon de test

In [63]:
test_monks3_knn = myKnn4.test(test4, test_labels4)

Matrice de confusion:
[[134.  70.]
 [ 70. 158.]]

Exactitude:
0.6759259259259259

Précision:
[0.6568627450980392, 0.6929824561403509]

Rappel:
[0.6568627450980392, 0.6929824561403509]

Calculé en:
0.4376678466796875s


## Congressional Voting Records Dataset

- On identifie la meilleure valeur de k

In [64]:
findbest_Knn = Knn.Knn()
meilleur_k = findbest_Knn.set_best_k(train5, 
                                     train_labels5, 
                                     nb_split=5, 
                                     k_potentiel=range(2,12))

Le meilleur k est: 10
Calculé en 0.2262570858001709s


In [65]:
myKnn5 = Knn.Knn(meilleur_k)

- On effectue l'entrainement du modèle

In [66]:
training_congres_knn = myKnn5.train(train5, train_labels5)

Matrice de confusion:
[[ 91.  18.]
 [ 17. 178.]]

Exactitude:
0.8848684210526315

Précision:
[0.8425925925925926, 0.9081632653061225]

Rappel:
[0.8348623853211009, 0.9128205128205128]

Calculé en:
1.389171838760376s


- On effectue maintenant le test avec l'échantillon de test

In [67]:
test_congres_knn = myKnn5.test(test5, test_labels5)

Matrice de confusion:
[[50.  9.]
 [ 8. 64.]]

Exactitude:
0.8702290076335878

Précision:
[0.8620689655172413, 0.8767123287671232]

Rappel:
[0.847457627118644, 0.8888888888888888]

Calculé en:
0.6056292057037354s


# Algorithme Bayes Naïf

Cet algorithme est basé sur la règle de Bayes:

$$
P(C|X) = \frac{P(X|C)P(C)}{P(X)}
$$

Dans notre cas, le dénominateur est une constante et ne nous intéresse pas. Nous le représentons par la lettre $\alpha$

En posant l'hypothèse de l'indépendance conditionnelle entre les caractéristiques $X_1,\ldots,X_m$, on peut réécrire la règle comme suit:

$$
P(C|X) = \alpha P(X) \prod_{f=1}^m P(X_f|C)
$$

Dans le cas de variables descriptives continues, la probabilité $P(X_f|C)$ prend plutôt la forme d'une distribution de probabilités. On utilisera alors la fonction de densité de probabilités de la loi gaussienne, avec la moyenne et l'écart-type estimés à partir des données.

## Pseudocode

### Initialisation

Il n'y a aucun paramètre à initialiser

### Entrainement

L'entrainement se fait en deux parties. On calcule d'abord les probabilités à priori des classes de l'étiquette $\mathbf{P}(C)$

```
T = copie jeu d'entrainement
L = copie des étiquettes d'entrainement
Pour c dans unique(L):
    Compteur=0
    Pour l dans L:
        Si l=c:
            Compteur+=1
    P(C=c) = Compteur/N
```

On calcule ensuite les probabilités conditionnelles des caractéristiques sachant la classe de l'étiquette $\mathbf{P}(F_1,\ldots,F_m|C)$

```
F <- Liste des caractéristiques
Pour c dans unique(L):
    TS <- filtrer(T si L=c)
    NS <- taille(TS)
    Pour f dans F:
        Si Gaussien:
            Parametres(C=c,F=f) = (moyenne(TS[f]), écart-type(TS[f]))
        Sinon:
            Pour v dans unique(TS[f]):
                Compteur = 0
                Pour l dans TS[f]:
                Si l=v:
                    Compteur+=1
            P(C=c,F=f,V=v) = Compteur/NS
```

Pour la prédiction, on ne calcule pas le facteur de régularisation $\alpha$ pour amener les probabilité à 1, car ce qui nous intéresse, c'est une relation d'ordre et celle-ci est inchangée si on la divise par un nombre positif.

### Prédiction

```
Pour c dans unique(L):
    Produit=0
    Pour f dans F:
        Pour l dans TS[f]:
        Si Gaussien:
            Si Parametres(C=c,F=f) existe:
                Produit *= Densité_Gaussien(l,Parametres(C=c,F=f))
        Sinon
            Si P(C=c,F=f,V=l) existe:
                Produit *= P(C=c,F=f,V=l)
    P(X|c) = Produit
Retourner c où P(X|c) = Max(P(X|C))
```

### Test

```
Pour chaque observation x_i, i=1,N:
    S_i <- Prédiction(x_i)
M <- matrice de confusion avec les étiquettes d'entrainement et les étiquettes S
Calculer les métriques depuis M
```

## Iris Dataset

Comme ce jeu de données présente des caractéristiques continues, on utilisera la variante gaussienne du Bayes Naif

In [68]:
BN = BayesNaif.BayesNaif(True)

Mesures de performance sur l'échantillon d'entrainement

In [69]:
train_iris_nb = BN.train(train1, train_labels1)

Matrice de confusion:
[[35.  0.  0.]
 [ 0. 31.  2.]
 [ 0.  3. 34.]]

Exactitude:
0.9523809523809523

Précision:
[1.0, 0.9117647058823529, 0.9444444444444444]

Rappel:
[1.0, 0.9393939393939394, 0.918918918918919]

Calculé en:
0.005628347396850586s


Mesures de performance sur l'échantillon de test

In [70]:
test_iris_nb = BN.test(test1,test_labels1)

Matrice de confusion:
[[15.  0.  0.]
 [ 0. 15.  2.]
 [ 0.  0. 13.]]

Exactitude:
0.9555555555555556

Précision:
[1.0, 1.0, 0.8666666666666667]

Rappel:
[1.0, 0.8823529411764706, 1.0]

Calculé en:
0.0021715164184570312s


## Monks Dataset

Comme ce jeu de données présente des caractéristiques discrètes, on n'utilise pas la variante gaussienne du Bayes Naif

### Premier sous-ensemble

In [71]:
BN2 = BayesNaif.BayesNaif(False)

In [72]:
train_monks1_nb = BN2.train(train2, train_labels2)

Matrice de confusion:
[[56.  6.]
 [37. 25.]]

Exactitude:
0.6532258064516129

Précision:
[0.6021505376344086, 0.8064516129032258]

Rappel:
[0.9032258064516129, 0.4032258064516129]

Calculé en:
0.0070645809173583984s


Mesures de performance sur l'échantillon de test

In [73]:
test_monks1_nb = BN2.test(test2,test_labels2)

Matrice de confusion:
[[165.  51.]
 [159.  57.]]

Exactitude:
0.5138888888888888

Précision:
[0.5092592592592593, 0.5277777777777778]

Rappel:
[0.7638888888888888, 0.2638888888888889]

Calculé en:
0.012335538864135742s


### Second sous-ensemble

In [74]:
BN3 = BayesNaif.BayesNaif(False)

In [75]:
train_monks2_nb = BN3.train(train3, train_labels3)

Matrice de confusion:
[[92. 13.]
 [48. 16.]]

Exactitude:
0.6390532544378699

Précision:
[0.6571428571428571, 0.5517241379310345]

Rappel:
[0.8761904761904762, 0.25]

Calculé en:
0.011017560958862305s


Mesures de performance sur l'échantillon de test

In [76]:
test_monks2_nb = BN3.test(test3,test_labels3)

Matrice de confusion:
[[244.  46.]
 [120.  22.]]

Exactitude:
0.6157407407407407

Précision:
[0.6703296703296703, 0.3235294117647059]

Rappel:
[0.8413793103448276, 0.15492957746478872]

Calculé en:
0.012041330337524414s


### Troisième sous-ensemble

In [77]:
BN4 = BayesNaif.BayesNaif(False)

In [78]:
train_monks3_nb = BN4.train(train4, train_labels4)

Matrice de confusion:
[[57.  5.]
 [ 3. 57.]]

Exactitude:
0.9344262295081968

Précision:
[0.95, 0.9193548387096774]

Rappel:
[0.9193548387096774, 0.95]

Calculé en:
0.007179975509643555s


Mesures de performance sur l'échantillon de test

In [79]:
test_monks3_nb = BN4.test(test4,test_labels4)

Matrice de confusion:
[[204.   0.]
 [ 12. 216.]]

Exactitude:
0.9722222222222222

Précision:
[0.9444444444444444, 1.0]

Rappel:
[1.0, 0.9473684210526315]

Calculé en:
0.011954069137573242s


## Congressional Voting Records Dataset

Comme ce jeu de données présente des caractéristiques discrètes, on n'utilise pas la variante gaussienne du Bayes Naif

In [80]:
BN5 = BayesNaif.BayesNaif(False)

In [81]:
train_congres_nb = BN5.train(train5, train_labels5)

Matrice de confusion:
[[100.   9.]
 [ 20. 175.]]

Exactitude:
0.9046052631578947

Précision:
[0.8333333333333334, 0.9510869565217391]

Rappel:
[0.9174311926605505, 0.8974358974358975]

Calculé en:
0.034026384353637695s


Mesures de performance sur l'échantillon de test

In [82]:
test_congres_nb = BN5.test(test5, test_labels5)

Matrice de confusion:
[[56.  3.]
 [ 7. 65.]]

Exactitude:
0.9236641221374046

Précision:
[0.8888888888888888, 0.9558823529411765]

Rappel:
[0.9491525423728814, 0.9027777777777778]

Calculé en:
0.004875659942626953s


# Conclusion

## Tableau sommaire

In [83]:
tous_resultats = [["Iris",test_iris_knn,test_iris_nb],
                  ["MONKS1",test_monks1_knn,test_monks1_nb],
                  ["MONKS2",test_monks2_knn,test_monks2_nb],
                  ["MONKS3",test_monks3_knn,test_monks3_nb],
                  ["Votes",test_congres_knn,test_congres_nb]]

### Exactitude

Le tableau ci-dessous présente l'exactitude pour les modèles KNN et NB ainsi que le meilleur modèle dans ce cas. On remarque que pour le jeu de données Iris, le résultat obtenu est le même pour les deux modèles. Pour les jeux MONKS, dans deux des trois cas, le modèle KNN est meilleur, mais les deux résultats sont faibles. Dans le troisième cas, le modèle NB est largement plus exact, une situation similaire se reproduit pour les données sur les votes.

In [84]:
print(np.array([(i[0],
           i[1][1],
           i[2][1],
           "KNN" if i[1][1]>i[2][1] else "NB") for i in tous_resultats]))

[['Iris' '0.9555555555555556' '0.9555555555555556' 'NB']
 ['MONKS1' '0.7083333333333334' '0.5138888888888888' 'KNN']
 ['MONKS2' '0.6921296296296297' '0.6157407407407407' 'KNN']
 ['MONKS3' '0.6759259259259259' '0.9722222222222222' 'NB']
 ['Votes' '0.8702290076335878' '0.9236641221374046' 'NB']]


### Précision

On obtient les mêmes constats que précédemment au niveau de la précision

In [85]:
print(np.array([(i[0],
           i[1][2],
           i[2][2],
           "KNN" if i[1][2]>i[2][2] else "NB") for i in tous_resultats]))

[['Iris' list([1.0, 1.0, 0.8666666666666667])
  list([1.0, 1.0, 0.8666666666666667]) 'NB']
 ['MONKS1' list([0.7393617021276596, 0.6844262295081968])
  list([0.5092592592592593, 0.5277777777777778]) 'KNN']
 ['MONKS2' list([0.689156626506024, 0.7647058823529411])
  list([0.6703296703296703, 0.3235294117647059]) 'KNN']
 ['MONKS3' list([0.6568627450980392, 0.6929824561403509])
  list([0.9444444444444444, 1.0]) 'NB']
 ['Votes' list([0.8620689655172413, 0.8767123287671232])
  list([0.8888888888888888, 0.9558823529411765]) 'NB']]


### Rappel

Pour le rappel, on obtient des résultats différents. Pour le jeu de données MONKS1, l'ordre des valeurs du rappel est inversé. Ceci nous montre qu'il est important de sélectionner la mesure la plus importante pour le problème que nous voulons résoudre, car il est possible d'obtenir un conclusion erronée en utilisant une autre.

In [86]:
print(np.array([(i[0],
           i[1][3],
           i[2][3],
           "KNN" if i[1][3]>i[2][3] else "NB") for i in tous_resultats]))

[['Iris' list([1.0, 0.8823529411764706, 1.0])
  list([1.0, 0.8823529411764706, 1.0]) 'NB']
 ['MONKS1' list([0.6435185185185185, 0.7731481481481481])
  list([0.7638888888888888, 0.2638888888888889]) 'NB']
 ['MONKS2' list([0.9862068965517241, 0.09154929577464789])
  list([0.8413793103448276, 0.15492957746478872]) 'KNN']
 ['MONKS3' list([0.6568627450980392, 0.6929824561403509])
  list([1.0, 0.9473684210526315]) 'NB']
 ['Votes' list([0.847457627118644, 0.8888888888888888])
  list([0.9491525423728814, 0.9027777777777778]) 'NB']]


### Temps d'exécution

Dans tous les cas, le temps de calcul du Naive Bayes est signicativement plus court.

In [87]:
print(np.array([(i[0],
           i[1][4],
           i[2][4],
           "KNN" if i[1][4]<i[2][4] else "NB") for i in tous_resultats]))

[['Iris' '0.04592633247375488' '0.0021715164184570312' 'NB']
 ['MONKS1' '0.4427499771118164' '0.012335538864135742' 'NB']
 ['MONKS2' '0.5991506576538086' '0.012041330337524414' 'NB']
 ['MONKS3' '0.4376678466796875' '0.011954069137573242' 'NB']
 ['Votes' '0.6056292057037354' '0.004875659942626953' 'NB']]


## Observations

- Le jeu de données Iris présente un problème de classification bien balancé. Les deux algorithmes sont performants et s'exécutent rapidement.
- Le jeu de données MONKS représentent des problèmes de classification binaire avec peu d'observations. Les algorithmes ne performent pas très bien lors des tests.
- Le jeu de données Congressional Voting Records contient davantage de caractéristiques, mais beaucoup moins de modalités. C'est aussi un problème de classification binaire. Un algorithme tel que KNN pourrait tirer des conclusions erronées étant donné que les distances entre les modalités sont toutes égales. 

## Difficultés rencontrées

### Algorithme kNN

Une des difficultés rencontrées a été d'avoir effectivement le bon nombre de voisins dans l'entraînement, car le jeu d'entrainement contient toujours l'exemple et a une distance de 0. J'ai donc du modifier l'ensemble d'entrainement pour enlever l'exemple actif lors du calcul des métriques. Ceci était nécessaire pour pouvoir calculer la meilleure valeur de $k$.

### Algorithme Bayes Naïf

Comme il est possible de rencontrer une classe jamais rencontrée lors de l'entraînement, j'ai du modifier le produite des probabilités conditionnelles indépendantes pour enlever les probabilités qui ne sont pas évaluées durant l'entraînement. J'aurais pu modifier le tableau de probabilités, mais le plus simple a été de leur donner une valeur de 1, ce qui est équivalent à les ignorer dans le produit.